In [148]:
import random

In [149]:
events = True
verbose = False
tiempos = False

#### Parámetros

In [150]:
# Ejemplo del enunciado
T = 30*24*60 # 24h en minutos
# T = 100 #un mes en minutos #pongo 1 dia

nPistas = 3
nCoches = 20
nPuertas = 50

# lambda0 = getlambda0(t)
mu11 = 10.007615178514001
sigma11 = 3.0377002745229005
a12 = 10
b12 = 15
lambda2 = 1 / 2
lambda3 = 0.1

# T, nCoches, nPuertas, mu11, sigma11, a12, b12, lambda2, lambda3

In [151]:
def getlambda0(t):
    # t está en minutos, convertir a horas:
    t = t/60
    t = t%24 ##########ojo esto##########
    # Intervalo de 0 a 5 horas, lineal de 5 a 7
    if 0 <= t < 5:
        return 5 + (7 - 5) * (t - 0) / (5 - 0)
    # Intervalo de 5 a 8 horas, lineal de 7 a 6
    elif 5 <= t < 8:
        return 7 + (6 - 7) * (t - 5) / (8 - 5)
    # Intervalo de 8 a 15 horas, lineal de 6 a 9
    elif 8 <= t < 15:
        return 6 + (9 - 6) * (t - 8) / (15 - 8)
    # Intervalo de 15 a 17 horas, lineal de 9 a 6
    elif 15 <= t < 17:
        return 9 + (6 - 9) * (t - 15) / (17 - 15)
    # Intervalo de 17 a 24 horas, lineal de 6 a 5
    elif 14 <= t <= 24:
        return 6 + (5 - 6) * (t - 17) / (24 - 17)
    # Si el tiempo está fuera del rango de 0 a 24 horas
    else:
        return 10E9  

#### Funciones auxiliares para generación de tiempos

In [152]:
# Funciones auxiliares generacion de tiempos
def t_llegada(t):
    return random.expovariate(getlambda0(t))*60 #nº muy pequeños, tiene sentido?

def t_aterrizaje():
    # return np.random.normal(mu11, sigma11)
    # return random.normalvariate(mu11, sigma11) 
    while True:  # Bucle infinito hasta obtener un número válido
        resultado = random.normalvariate(mu11, sigma11)
        if resultado > 0:  # Comprobar si el resultado es mayor que cero
            return resultado
        
def t_traslado(): #N1- N2
    return random.expovariate(1/lambda2)

def t_desembarques():
    return random.expovariate(1/lambda3)

def t_salidas():
    return random.uniform(a12, b12)

#### Variables

In [153]:
def reiniciar_variables():
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3, aviones_en_n1, aviones_en_n2, aviones_en_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    t = 0                   # Variable reloj. tiempo asíncrono.
    n1 = n2 = n3 = 0        # Variables de estado nº clientes
    NLL1 = NLL2 = NLL3 = 0  # Variables contador nº llegadas
    NS1 = NS2 = NS3 = 0     # Variables contador nº salidas

    # Lista de tiempos de eventos
    LISTA = {
        'tLL1': 10E9,   
        'tS1':  [10E9]*nPistas,
        'tS2':  [10E9]*nCoches,
        'tS3':  [10E9]*nPuertas,
        'tSS':  [10E9]*nPistas
    }

    # Arrays for arrival and departure times
    LL1 = [] # tiempo de llegada de aviones
    LL2 = []
    LL3 = []
    S1 = []
    S2 = []
    S3 = [] # tiempo de llegada a la pista para despegar

    #Landing and departure times
    LANDING = []
    DEPARTURE = []

    # Colas
    esperando_a_despegar = 0
    esperando_a_aterrizar = 0
    esperando_coche = 0
    esperando_puerta = 0

    n_med_n1 = n_med_n2 = n_med_n3 = 0 # nº medio de aviones en el aeropuerto

    acumulo_pistas_ocupadas = cambio_pistas_ocupadas = 0
    aviones_en_n1 = []
    aviones_en_n2 = []
    aviones_en_n3 = []




#### Rutina de aterrizaje

In [154]:

def rutina_aterrizaje(t_suc):
    
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3, aviones_en_n1, aviones_en_n2, aviones_en_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    # para luego calcular numero medio de clientes
    n_med_n1 += n1 * (t_suc - t) #tiempo trascurrido hasta el suceso * nº aviones
    n_med_n2 += n2 * (t_suc - t)
    n_med_n3 += n3 * (t_suc - t)
    
    LL1.append(t_suc) #anoto tiempo de llegada
    # Si tengo pista libre, aterrizo
    if (n1 < nPistas):
        # Actualizo variables contadores
        n1 += 1                     # El avión entra en n1, y ocupa una pista.ç
        aviones_en_n1.append((t_suc, 'entra'))
        
        if verbose: print(f'#### {n1} aviones en el nodo 1 ###')
        NLL1 += 1                   # numero de llegadas al n1
        if cambio_pistas_ocupadas > 0:
            acumulo_pistas_ocupadas += t_suc - cambio_pistas_ocupadas
            if tiempos: print(f'PISTA LIBRE AT {t_suc}. Acumulo {t_suc - cambio_pistas_ocupadas} -> {acumulo_pistas_ocupadas}')
            cambio_pistas_ocupadas = 0
            
        # LL1.append(t_suc)
        t = t_suc
        Z = t_aterrizaje() #random.normalvariate(mu11, sigma11) #genero tiempo aterrizaje
        LISTA['tS1'][LISTA['tS1'].index(10E9)] = t + Z
        
        LANDING.append(t) #anoto el tiempo en el que comienza el aterrizaje
        
        if events: print(f'ATERRIZAJE: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')
    
    # si no tengo pista, no aterrizo, me pongo en cola aterrizaje
    else:
        esperando_a_aterrizar+=1
        #si ya estaban ocupadas de antes, no actualices y quédate con el primero
        if cambio_pistas_ocupadas > 0 and t_suc > 0: 
            cambio_pistas_ocupadas = min(t_suc, cambio_pistas_ocupadas)
            if tiempos: print(f'Pista ocupada despegue en (t_suc, cambio) {t_suc, cambio_pistas_ocupadas} pero lo estaba antes en {cambio_pistas_ocupadas}')
        #si no lo estaban, actualiza el tiempo
        cambio_pistas_ocupadas = t_suc
        if tiempos: print(f'NO HAY PISTAS LIBRES at {cambio_pistas_ocupadas}')
        if events: print(f'ESPERANDO ATERRIZAR: {esperando_a_aterrizar} aviones esperando. Minuto {t}')
    #=========================================================================#

    # Genero tiempo siguente llegada
    Y = t_llegada(t)
    # Compruebo si el siguiente avión llega antes de T
    if (t + Y < T):
        LISTA['tLL1'] = t + Y #añado otro tiempo de llegada
        # print(f'NUEVO AVIÓN: Minuto: {t+Y}')
    else:
        if events: print(f'#### HORIZONTE ALCANZADO: {t+Y} > {T}, no llegan más aviones ####')
        if verbose: print(f'#### n1 = {n1}, n2 = {n2}, n3 = {n3} ####')
        if verbose: print(LISTA)


#### Rutina de traslado

In [155]:
def rutina_traslado(t_suc): 
    # un coche recoge al avión y lo desaloja de la pista (salida de N1)
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3, aviones_en_n1, aviones_en_n2, aviones_en_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    n_med_n1 += n1 * (t_suc - t) #tiempo trascurrido hasta el suceso * nº aviones
    n_med_n2 += n2 * (t_suc - t)
    n_med_n3 += n3 * (t_suc - t)
    
    t=t_suc     # Actualizamos tº de simulación
    n1 -=1      # El avión sale del nodo 1, y despeja una pista
    aviones_en_n1.append((t_suc, 'sale'))
    
    if cambio_pistas_ocupadas > 0:
        acumulo_pistas_ocupadas += t_suc - cambio_pistas_ocupadas
        if tiempos: print(f'PISTA LIBRE AT {t_suc}. Acumulo {t_suc - cambio_pistas_ocupadas} -> {acumulo_pistas_ocupadas}')
        cambio_pistas_ocupadas = 0
    # si hay coches disponibles -> traslado
    if n2 < nCoches:
        
        n2 +=1                  # El avion entra en n2, y ocupa un coche
        aviones_en_n2.append((t, 'entra'))
        # tiempo de salida del N2, que se corresponde con el final del traslado
        Z = t_traslado()
        LISTA['tS2'][LISTA['tS2'].index(10E9)] = t + Z 

        if events: print(f'-TRASLADO: {n2} coches ocupados. Minuto {t}. Fin de traslado {t+Z}')
        
    else: #si no hay coche disponibles 
        esperando_coche +=1 #lo pongo a la cola de ser trasladado
        if events: print('-ESPERANDO COCHE: {esperando_coche} aviones esperando. Minuto {t}')

    if esperando_a_aterrizar > 0: # ahora que se han liberado pistas, atendemos a la cola de aterrizaje
        Z = t_aterrizaje()                              # genero tiempo que tardará en aterrizar
        LISTA['tS1'][LISTA['tS1'].index(10E9)] = t + Z  # registro el tiempo en el que saldrá el avión del nodo 1
        LANDING.append(t)
        n1+=1                       # El avión en cola entra al n1, ocupa una pista,
        aviones_en_n1.append((t, 'entra'))
        esperando_a_aterrizar -= 1  # y libera su puesto en la cola.
        if events: print(f'ATERRIZAJE_cola: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')
        
    elif esperando_a_despegar > 0:

        if esperando_a_aterrizar>0: return -1
        
        n1+=1                       # El avión en cola entra al n1, ocupa una pista,
        aviones_en_n1.append((t, 'entra'))
        esperando_a_despegar -=1    # Y libera su puesto en la cola.
        DEPARTURE.append(t)         # Registro tiempo en el que empieza a despegar
        Z = t_salidas()                                 # genero tiempo que tardará en despegar
        LISTA['tSS'][LISTA['tSS'].index(10E9)] = t + Z  # registro el tiempo en el que saldrá el avión del nodo 1

        
        if events: print(f'---DESPEGUE_cola: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')
        

#### Rutina de desembarque

In [156]:
def rutina_desembarque(t_suc): 
    # avion en aeropuerto: desembarcan pasajeros, embarcan los nuevos y traslado a pistas
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3, aviones_en_n1, aviones_en_n2, aviones_en_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    n_med_n1 += n1 * (t_suc - t) #tiempo trascurrido hasta el suceso * nº aviones
    n_med_n2 += n2 * (t_suc - t)
    n_med_n3 += n3 * (t_suc - t)
    
    t=t_suc     # Actualizamos tº de simulación
    
    n2 -=1      # El avión sale de n2 y libera su vehículo.
    aviones_en_n2.append((t, 'sale'))
    
    #si hay puertas de embarque disponibles
    if n3 < nPuertas:

        n3 +=1      # El avión entra en n3, y ocupa una puerta
        aviones_en_n3.append((t, 'entra'))
        
        Z = t_desembarques()
        LISTA['tS3'][LISTA['tS3'].index(10E9)] = t + Z

        if events: print(f'--PUERTA ASIGNADA: {n3} puertas ocupadas. Minuto: {t}. Fin de proceso: {t+Z}')
        
    else: # si no hay puertas disponibles 
        esperando_puerta+=1     # esperando puerta embarque
        if events: print(f'--ESPERANDO PUERTA: {esperando_puerta} aviones esperando. Minuto: {t}')

    # si tengo aviones pendientes de ser trasladados
    if esperando_coche > 0: 

        n2+=1                       # El avión en cola entra al n2, ocupa un coche,
        aviones_en_n2.append((t, 'entra'))
        esperando_coche -= 1        # Y libera su puesto en la cola.
        
        Y = t_traslado()
        LISTA['tS2'][LISTA['tS2'].index(10E9)] = t + Y

        if events: print(f'-TRASLADO_cola: {n2} coches ocupados. Minuto {t}. Fin de traslado {t+Z}')

#### Rutina de despegue (vuelta al nodo 1)

In [157]:
def rutina_despegue(t_suc): 
    # sale del nodo 3 y espera a poder salir del sistema (nodo SS)    
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3, aviones_en_n1, aviones_en_n2, aviones_en_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    n_med_n1 += n1 * (t_suc - t) #tiempo trascurrido hasta el suceso * nº aviones
    n_med_n2 += n2 * (t_suc - t)
    n_med_n3 += n3 * (t_suc - t)
    
    
    t=t_suc     # Actualizamos tº de simulación

    n3 -=1      # El avión sale del n3 y libera un puerta.
    aviones_en_n3.append((t, 'sale'))
    
    S3.append(t)
    
    # Si hay pistas libres
    if n1 < nPistas:
        
        n1+=1               # El avión entra al n1 y ocupa una pista
        aviones_en_n1.append((t_suc, 'entra'))
        
        if cambio_pistas_ocupadas > 0:
            acumulo_pistas_ocupadas += t_suc - cambio_pistas_ocupadas
            if tiempos: print(f'PISTA LIBRE AT {t_suc}. Acumulo {t_suc - cambio_pistas_ocupadas} -> {acumulo_pistas_ocupadas}')
            cambio_pistas_ocupadas = 0

        # generamos tiempo de despegue
        Z = t_salidas()
        LISTA['tSS'][LISTA['tSS'].index(10E9)] = t + Z
        DEPARTURE.append(t)
        if events: print(f'---DESPEGUE: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')

    else:    
        esperando_a_despegar+=1 #esperando para el despegue
        #si ya estaban ocupadas de antes, no actualices y quédate con el primero
        if cambio_pistas_ocupadas > 0 and t_suc > 0: 
            cambio_pistas_ocupadas = min(t_suc, cambio_pistas_ocupadas)
            if tiempos: print(f'Pista ocupada despegue en (t_suc, cambio) {t_suc, cambio_pistas_ocupadas} pero lo estaba antes en {cambio_pistas_ocupadas}')
        #si no lo estaban, actualiza el tiempo
        cambio_pistas_ocupadas = t_suc
        if tiempos: print(f'NO HAY PISTAS LIBRES at {cambio_pistas_ocupadas}')
        if events: print(f'---ESPERANDO DESPEGAR: {esperando_a_despegar} aviones esperando. Minuto: {t}')

    # Manejo la cola del nodo anterior
    # si quedan aviones esperando puerta
    if esperando_puerta > 0:
        
        n3+=1                   # El avion entra al n3, ocupa una puerta
        aviones_en_n3.append((t, 'entra'))
        esperando_puerta-=1     # Y libera su puesto en la cola

        Y = t_desembarques()    # Genero tiempo de desembarque
        LISTA['tS3'][LISTA['tS3'].index(10E9)] = t + Y

        if events: print(f'--PUERTA ASIGNADA_cola: {n3} puertas ocupadas. Minuto: {t}. Fin de proceso: {t+Z}')

#### Rutina de salida

In [158]:
def rutina_salida_sistema(t_suc): 
    # sale del nodo 3 y espera a poder salir del sistema (nodo SS)    
    global t, n1, n2, n3, NLL1, LL1, LISTA, LANDING, S3, DEPARTURE, acumulo_pistas_ocupadas, cambio_pistas_ocupadas
    global n_med_n1, n_med_n2, n_med_n3, aviones_en_n1, aviones_en_n2, aviones_en_n3
    global esperando_a_despegar, esperando_a_aterrizar, esperando_coche, esperando_puerta
    
    n_med_n1 += n1 * (t_suc - t) #tiempo trascurrido hasta el suceso * nº aviones
    n_med_n2 += n2 * (t_suc - t)
    n_med_n3 += n3 * (t_suc - t)
    
    t=t_suc     # Actualizamos tº de simulación

    n1 -=1      # El avión sale del nodo 1 y despeja una pista.
    aviones_en_n1.append((t, 'sale'))
    
    if events: print(f'----SALIDA DE SISTEMA: {n1} pistas ocupadas. Minuto: {t}.')

    if events: print(f'---------------------: Esperando aterrizar: {esperando_a_aterrizar}, Esperando despegar: {esperando_a_despegar}')

    # Manejo la cola del nodo anterior  
    if esperando_a_aterrizar > 0: # ahora que se han liberado pistas, atendemos a la cola de aterrizaje
        Z = t_aterrizaje()                              # genero tiempo que tardará en aterrizar
        LISTA['tS1'][LISTA['tS1'].index(10E9)] = t + Z  # registro el tiempo en el que saldrá el avión del nodo 1
        LANDING.append(t)
        n1+=1                       # El avión en cola entra al n1, ocupa una pista,
        aviones_en_n1.append((t, 'entra'))
        esperando_a_aterrizar -= 1  # y libera su puesto en la cola.

        if events: print(f'ATERRIZAJE_cola: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')
        
    elif esperando_a_despegar > 0:

        if esperando_a_aterrizar>0: return -1
        
        n1+=1                       # El avión en cola entra al n1, ocupa una pista,
        aviones_en_n1.append((t, 'entra'))
        esperando_a_despegar -=1    # Y libera su puesto en la cola.
        
        DEPARTURE.append(t)
        
        Z = t_salidas()                                 # genero tiempo que tardará en despegar
        LISTA['tSS'][LISTA['tSS'].index(10E9)] = t + Z  # registro el tiempo en el que saldrá el avión del nodo 1

        
        if events: print(f'---DESPEGUE_cola: {n1} pistas ocupadas. Minuto: {t}. Fin de maniobra: {t+Z}')


# MAIN

In [159]:

def simul_main():
    global LISTA

    reiniciar_variables()
    
    # Genero primer evento (aterrizaje)
    X = t_llegada(0)
    
    # Caso especial
    if X > T:
        return
    
    rutina_aterrizaje(X)

    # Bucle principal
    # While haya eventos pendientes (tiempos en la lista)
    while any(min(val) != 10E9 if isinstance(val, list) else val != 10E9 for val in LISTA.values()):
        min_key = min(
            LISTA.keys(), 
            key=lambda k: min(LISTA[k]) if isinstance(LISTA[k], list) else LISTA[k]
        )
        if verbose: print(LISTA)
        if verbose: print(min_key, LISTA[min_key])
        if verbose: print ()

        if(min_key=='tLL1'): # Si el próximo evento es un aterrizaje (LLN1)
            t_suc=LISTA['tLL1']
            LISTA['tLL1']= 10E9
            rutina_aterrizaje(t_suc)
            
        elif(min_key=='tS1'): # Si el próximo evento es un traslado (SN1)
            t_suc=min(LISTA['tS1'])
            LISTA['tS1'][LISTA['tS1'].index(min(LISTA['tS1']))] = 10E9
            rutina_traslado(t_suc)
            
        elif(min_key=='tS2'): # Si el próximo evento es un desembarque (SN2)
            t_suc=min(LISTA['tS2'])
            LISTA['tS2'][LISTA['tS2'].index(min(LISTA['tS2']))] = 10E9
            rutina_desembarque(t_suc)
            
        elif(min_key=='tS3'): # Si el próximo evento es una preparación para despegue (SN3)
            t_suc=min(LISTA['tS3'])
            LISTA['tS3'][LISTA['tS3'].index(min(LISTA['tS3']))] = 10E9
            rutina_despegue(t_suc)
            
        elif(min_key=='tSS'): # Si el próximo evento es una salida de sistema (SN4)
            t_suc=min(LISTA['tSS'])
            LISTA['tSS'][LISTA['tSS'].index(min(LISTA['tSS']))] = 10E9
            rutina_salida_sistema(t_suc)    

In [160]:
simul_main()
Tp = max(0,t-T)
print('----El horizonte temporal de la simulación eran '+ str(round(T/60,2)) + 'h ~ '+str(T)+' minutos.----')
print('----La simulación ha terminado completamente en el minuto '+ str(T + Tp) + ' ~ '+str(round(T + Tp/60,2))+'h.----')

ATERRIZAJE: 1 pistas ocupadas. Minuto: 0.4698605010292748. Fin de maniobra: 12.312099625347606
ATERRIZAJE: 2 pistas ocupadas. Minuto: 5.253380583213706. Fin de maniobra: 18.09913527481276
-TRASLADO: 1 coches ocupados. Minuto 12.312099625347606. Fin de traslado 12.51161315013743
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 12.51161315013743. Fin de proceso: 13.185839397950026
---DESPEGUE: 2 pistas ocupadas. Minuto: 13.185839397950026. Fin de maniobra: 25.584982338599723
ATERRIZAJE: 3 pistas ocupadas. Minuto: 15.580748594565687. Fin de maniobra: 24.298597173845074
-TRASLADO: 1 coches ocupados. Minuto 18.09913527481276. Fin de traslado 18.147376637340255
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 18.147376637340255. Fin de proceso: 18.264262838333266
---DESPEGUE: 3 pistas ocupadas. Minuto: 18.264262838333266. Fin de maniobra: 31.40400139846568
ESPERANDO ATERRIZAR: 1 aviones esperando. Minuto 18.264262838333266
-TRASLADO: 1 coches ocupados. Minuto 24.298597173845074. Fin de traslado 


---DESPEGUE_cola: 3 pistas ocupadas. Minuto: 2095.2235403721816. Fin de maniobra: 2106.1238187485847
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 2095.385016371913. Fin de proceso: 2095.495140927695
---ESPERANDO DESPEGAR: 68 aviones esperando. Minuto: 2095.495140927695
-TRASLADO: 1 coches ocupados. Minuto 2097.4459780270354. Fin de traslado 2097.8677823633016
---DESPEGUE_cola: 3 pistas ocupadas. Minuto: 2097.4459780270354. Fin de maniobra: 2110.8612605064845
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 2097.8677823633016. Fin de proceso: 2097.9200782362495
---ESPERANDO DESPEGAR: 68 aviones esperando. Minuto: 2097.9200782362495
ESPERANDO ATERRIZAR: 1 aviones esperando. Minuto 2097.9200782362495
ESPERANDO ATERRIZAR: 2 aviones esperando. Minuto 2097.9200782362495
ESPERANDO ATERRIZAR: 3 aviones esperando. Minuto 2097.9200782362495
ESPERANDO ATERRIZAR: 4 aviones esperando. Minuto 2097.9200782362495
----SALIDA DE SISTEMA: 2 pistas ocupadas. Minuto: 2103.245444455823.
-------------------

In [161]:
print(f'n med en n1 = {n_med_n1/t}, n med en n2 = {n_med_n2/t}, n med en n3 = {n_med_n3/t}. TOTAL = {(n_med_n1 + n_med_n2 + n_med_n3)/t}')

n med en n1 = 3.974516892709757, n med en n2 = 0.06950281524944156, n med en n3 = 0.013482551237746717. TOTAL = 4.057502259196945


Número medio de aviones por cada nodo

In [162]:
aviones_en_n1
# Inicializa contadores
contador_entra = 0
contador_sale = 0

# Iterar sobre la lista de eventos
for tiempo, tipo_evento in aviones_en_n1:
    if tipo_evento == 'entra':
        contador_entra += 1  # Contar entradas
    elif tipo_evento == 'sale':
        contador_sale += 1  # Contar salidas

# Calcular aviones que han pasado por n1
total_aviones = contador_entra - contador_sale

print(f"Número total de aviones que han pasado por n1: {contador_entra}, {contador_entra/2} que llegan y que luego se vuelven a ir")

# Variables
contador_aviones = 0  # Número de aviones en n1
total_avion_minutos = 0  # Total de avión-minutos
tiempo_anterior = 0  # Tiempo del último evento
capacidad_nodo = nPistas  # Capacidad del nodo n1

# Iterar sobre la lista de eventos
for tiempo, tipo_evento in aviones_en_n1:
    # Calcular cuánto tiempo los aviones han estado en n1
    duracion_estado = tiempo - tiempo_anterior
    total_avion_minutos += contador_aviones * duracion_estado

    # Actualizar el número de aviones según el evento
    if tipo_evento == 'entra':
        if contador_aviones < capacidad_nodo:  # Solo entrar si hay espacio
            contador_aviones += 1
    elif tipo_evento == 'sale':
        if contador_aviones > 0:  # Solo salir si hay aviones
            contador_aviones -= 1
    
    # Actualiza el tiempo anterior al tiempo del evento actual
    tiempo_anterior = tiempo

# Considerar el tiempo total hasta el último evento
tiempo_final = t  
duracion_estado = tiempo_final - tiempo_anterior
total_avion_minutos += contador_aviones * duracion_estado

# Cálculo del número medio de aviones en el nodo n1
numero_medio_aviones = total_avion_minutos / tiempo_final

print(f"Número medio de aviones en n1: {numero_medio_aviones:.2f}")

Número total de aviones que han pasado por n1: 12492, 6246.0 que llegan y que luego se vuelven a ir
Número medio de aviones en n1: 2.98


In [163]:
aviones_en_n2
# Inicializa contadores
contador_entra = 0
contador_sale = 0

# Iterar sobre la lista de eventos
for tiempo, tipo_evento in aviones_en_n2:
    if tipo_evento == 'entra':
        contador_entra += 1  # Contar entradas
    elif tipo_evento == 'sale':
        contador_sale += 1  # Contar salidas

# Calcular aviones que han pasado por n1
total_aviones = contador_entra - contador_sale

print(f"Número total de aviones que han pasado por n2: {contador_entra}.")

# Variables
contador_aviones = 0  # Número de aviones en n2
total_avion_minutos = 0  # Total de avión-minutos
tiempo_anterior = 0  # Tiempo del último evento
capacidad_nodo = nCoches  # Capacidad del nodo n2

# Iterar sobre la lista de eventos
for tiempo, tipo_evento in aviones_en_n2:
    # Calcular cuánto tiempo los aviones han estado en n1
    duracion_estado = tiempo - tiempo_anterior
    total_avion_minutos += contador_aviones * duracion_estado

    # Actualizar el número de aviones según el evento
    if tipo_evento == 'entra':
        if contador_aviones < capacidad_nodo:  # Solo entrar si hay espacio
            contador_aviones += 1
    elif tipo_evento == 'sale':
        if contador_aviones > 0:  # Solo salir si hay aviones
            contador_aviones -= 1
    
    # Actualiza el tiempo anterior al tiempo del evento actual
    tiempo_anterior = tiempo

# Considerar el tiempo total hasta el último evento
tiempo_final = t  
duracion_estado = tiempo_final - tiempo_anterior
total_avion_minutos += contador_aviones * duracion_estado

# Cálculo del número medio de aviones en el nodo n2
numero_medio_aviones = total_avion_minutos / tiempo_final

print(f"Número medio de aviones en n2: {numero_medio_aviones:.2f}")

Número total de aviones que han pasado por n2: 6246.
Número medio de aviones en n2: 0.07


In [164]:
aviones_en_n3
# Inicializa contadores
contador_entra = 0
contador_sale = 0

# Iterar sobre la lista de eventos
for tiempo, tipo_evento in aviones_en_n3:
    if tipo_evento == 'entra':
        contador_entra += 1  # Contar entradas
    elif tipo_evento == 'sale':
        contador_sale += 1  # Contar salidas

# Calcular aviones que han pasado por n1
total_aviones = contador_entra - contador_sale

print(f"Número total de aviones que han pasado por n3: {contador_entra}.")

# Variables
contador_aviones = 0  # Número de aviones en n3
total_avion_minutos = 0  # Total de avión-minutos
tiempo_anterior = 0  # Tiempo del último evento
capacidad_nodo = nPuertas  # Capacidad del nodo n3

# Iterar sobre la lista de eventos
for tiempo, tipo_evento in aviones_en_n3:
    # Calcular cuánto tiempo los aviones han estado en n1
    duracion_estado = tiempo - tiempo_anterior
    total_avion_minutos += contador_aviones * duracion_estado

    # Actualizar el número de aviones según el evento
    if tipo_evento == 'entra':
        if contador_aviones < capacidad_nodo:  # Solo entrar si hay espacio
            contador_aviones += 1
    elif tipo_evento == 'sale':
        if contador_aviones > 0:  # Solo salir si hay aviones
            contador_aviones -= 1
    
    # Actualiza el tiempo anterior al tiempo del evento actual
    tiempo_anterior = tiempo

# Considerar el tiempo total hasta el último evento
tiempo_final = t  
duracion_estado = tiempo_final - tiempo_anterior
total_avion_minutos += contador_aviones * duracion_estado

# Cálculo del número medio de aviones en el nodo n2
numero_medio_aviones = total_avion_minutos / tiempo_final

print(f"Número medio de aviones en n3: {numero_medio_aviones:.2f}")

Número total de aviones que han pasado por n3: 6246.
Número medio de aviones en n3: 0.01


Tiempos de espera y % de tiempo pistas ocupadas

In [165]:
t_espera_aterrizaje = [a - b for a, b in zip(LANDING, LL1)]
print(f'{len(t_espera_aterrizaje)} aviones han aterrizado')
print(f'El tiempo máximo de espera de aterrizaje ha sido de {round(max(t_espera_aterrizaje),2)} minutos ~ {round(max(t_espera_aterrizaje)/60,2)}h.')
print(f'El tiempo medio de espera de aterrizaje ha sido de {round(sum(t_espera_aterrizaje)/len(t_espera_aterrizaje),2)} minutos ~ {round(sum(t_espera_aterrizaje)/len(t_espera_aterrizaje)/60,2)}h.')
print()
t_espera_despegue = [a - b for a, b in zip(DEPARTURE, S3)]
print(f'{len(t_espera_despegue)} aviones han despegado')
print(f'El tiempo máximo de espera de despegue ha sido de {round(max(t_espera_despegue),2)} minutos ~ {round(max(t_espera_despegue)/60,2)}h.')
print(f'El tiempo medio de espera de despegue ha sido de {round(sum(t_espera_despegue)/len(t_espera_despegue),2)} minutos ~ {round(sum(t_espera_despegue)/len(t_espera_despegue)/60,2)}h.')
print()
print(f'Las pistas han estado ocupadas durante {round(acumulo_pistas_ocupadas, 2)} minutos ~ {round(acumulo_pistas_ocupadas/60,2)}h.')
print(f'Esto es un porcentaje de tiempo del {round(acumulo_pistas_ocupadas*100/t,2)}%.')

6246 aviones han aterrizado
El tiempo máximo de espera de aterrizaje ha sido de 83.9 minutos ~ 1.4h.
El tiempo medio de espera de aterrizaje ha sido de 9.16 minutos ~ 0.15h.

6246 aviones han despegado
El tiempo máximo de espera de despegue ha sido de 6143.11 minutos ~ 102.39h.
El tiempo medio de espera de despegue ha sido de 3166.04 minutos ~ 52.77h.

Las pistas han estado ocupadas durante 22022.09 minutos ~ 367.03h.
Esto es un porcentaje de tiempo del 46.95%.


# TESTS

In [166]:
T=30*24*60
nCoches = nCoches + 5
nPistas = nPistas + 1
simul_main()
Tp = max(0,t-T)
print('----El horizonte temporal de la simulación eran '+ str(round(T/60,2)) + 'h ~ '+str(T)+' minutos.----')
print('----La simulación ha terminado completamente en el minuto '+ str(T + Tp) + ' ~ '+str(round(T + Tp/60,2))+'h.----')

ATERRIZAJE: 1 pistas ocupadas. Minuto: 19.25256617384208. Fin de maniobra: 25.30196384436791
ATERRIZAJE: 2 pistas ocupadas. Minuto: 20.54309723411639. Fin de maniobra: 32.16363693806886
ATERRIZAJE: 3 pistas ocupadas. Minuto: 23.634167734164013. Fin de maniobra: 32.67441219850284
-TRASLADO: 1 coches ocupados. Minuto 25.30196384436791. Fin de traslado 25.52668601782073
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 25.52668601782073. Fin de proceso: 25.557960731626125
---DESPEGUE: 3 pistas ocupadas. Minuto: 25.557960731626125. Fin de maniobra: 37.471063737159575
-TRASLADO: 1 coches ocupados. Minuto 32.16363693806886. Fin de traslado 32.404598574063066
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 32.404598574063066. Fin de proceso: 32.41923797115777
---DESPEGUE: 3 pistas ocupadas. Minuto: 32.41923797115777. Fin de maniobra: 47.2485978315155
-TRASLADO: 1 coches ocupados. Minuto 32.67441219850284. Fin de traslado 33.00505196577725
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 33.00505196


---DESPEGUE_cola: 4 pistas ocupadas. Minuto: 3238.8341968894742. Fin de maniobra: 3252.9248259265228
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 3239.1439901969534. Fin de proceso: 3239.172875985899
---ESPERANDO DESPEGAR: 12 aviones esperando. Minuto: 3239.172875985899
-TRASLADO: 1 coches ocupados. Minuto 3240.852443899644. Fin de traslado 3241.0163753981983
---DESPEGUE_cola: 4 pistas ocupadas. Minuto: 3240.852443899644. Fin de maniobra: 3251.0775468341735
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 3241.0163753981983. Fin de proceso: 3241.041976136655
---ESPERANDO DESPEGAR: 12 aviones esperando. Minuto: 3241.041976136655
-TRASLADO: 1 coches ocupados. Minuto 3245.758899347896. Fin de traslado 3246.335267021776
---DESPEGUE_cola: 4 pistas ocupadas. Minuto: 3245.758899347896. Fin de maniobra: 3257.1855886781573
--PUERTA ASIGNADA: 1 puertas ocupadas. Minuto: 3246.335267021776. Fin de proceso: 3246.6022719494763
---ESPERANDO DESPEGAR: 12 aviones esperando. Minuto: 3246.6022719494763


In [167]:
print(f'Simulación con {nCoches} vehículos y {nPistas} pistas')
print()
t_espera_aterrizaje = [a - b for a, b in zip(LANDING, LL1)]
print(f'{len(t_espera_aterrizaje)} aviones han aterrizado')
print(f'El tiempo máximo de espera de aterrizaje ha sido de {round(max(t_espera_aterrizaje),2)} minutos ~ {round(max(t_espera_aterrizaje)/60,2)}h.')
print(f'El tiempo medio de espera de aterrizaje ha sido de {round(sum(t_espera_aterrizaje)/len(t_espera_aterrizaje),2)} minutos ~ {round(sum(t_espera_aterrizaje)/len(t_espera_aterrizaje)/60,2)}h.')
print()
t_espera_despegue = [a - b for a, b in zip(DEPARTURE, S3)]
print(f'{len(t_espera_despegue)} aviones han despegado')
print(f'El tiempo máximo de espera de despegue ha sido de {round(max(t_espera_despegue),2)} minutos ~ {round(max(t_espera_despegue)/60,2)}h.')
print(f'El tiempo medio de espera de despegue ha sido de {round(sum(t_espera_despegue)/len(t_espera_despegue),2)} minutos ~ {round(sum(t_espera_despegue)/len(t_espera_despegue)/60,2)}h.')
print()
print(f'Las pistas han estado ocupadas durante {round(acumulo_pistas_ocupadas, 2)} minutos ~ {round(acumulo_pistas_ocupadas/60,2)}h.')
print(f'Esto es un porcentaje de tiempo del {round(acumulo_pistas_ocupadas*100/t,2)}%.')

Simulación con 25 vehículos y 4 pistas

5085 aviones han aterrizado
El tiempo máximo de espera de aterrizaje ha sido de 47.92 minutos ~ 0.8h.
El tiempo medio de espera de aterrizaje ha sido de 2.55 minutos ~ 0.04h.

5085 aviones han despegado
El tiempo máximo de espera de despegue ha sido de 277.54 minutos ~ 4.63h.
El tiempo medio de espera de despegue ha sido de 23.45 minutos ~ 0.39h.

Las pistas han estado ocupadas durante 10032.3 minutos ~ 167.2h.
Esto es un porcentaje de tiempo del 23.22%.
